In [1]:
# !pip install numpy==1.23.5
# !pip install protobuf==3.19.*
#!pip install protobuf==3.19.0
#!pip install pyyaml h5py
import tensorflow as tf
from keras.utils.np_utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.metrics import Recall, Precision 

import os
import pickle
import pandas as pd
import numpy as np
from model_team14 import *

In [2]:


# ## select imputed & transformed data
# X=pd.read_csv('../data/X_data_tr.csv', index_col='date', parse_dates=True)
# y=pd.read_csv('../data/y_data_tr.csv', index_col='date', parse_dates=True)
# threshold=0.2
# criteria=None

# metadata=pd.read_csv('../data/full_info.csv')
# df_feature=select_features(metadata, X, threshold, criteria=criteria)

def get_data(X, y, y_type, test_year, features):
    X_train=X[features][:-(test_year*12)]
    y_train=y[y_type][:-(test_year*12)]           
    X_test=X[features][-(test_year*12):]   
    y_test=y[y_type][-(test_year*12):]

    return X_train, y_train, X_test, y_test

In [3]:
## time_step means the length(n) of explanatory variables(t-(n-1) ~ t) to use for classifying y in certain time(t) period.

def create_dataset(X, y, time_steps=1):
    Xs, ys = [], []
    for i in range(len(X) - time_steps):
        v = X.iloc[i:(i + time_steps)].values
        Xs.append(v)        
        ys.append(y.iloc[i + time_steps])
    return np.array(Xs), np.array(ys)

In [4]:
def grid_search(path, trainX, trainy, testX, testy, y_type, nl=[50,100], epochs=[100,300], batch_sizes=[10], time_steps=[18,24],
                n_layer=[50,100]):
    results = []
    best_auc = 0
    best_params = None
    nc=len(trainy.unique())


    for time_step in time_steps:
        X_train, y_train = create_dataset(trainX, trainy, time_step)
        X_test, y_test = create_dataset(testX, testy, time_step)
        y_train = to_categorical(y_train, num_classes=nc)
        y_test = to_categorical(y_test, num_classes=nc)
        
        loss_type = 'categorical_crossentropy'   ##if y_type == 'y_agg' else 'binary_crossentropy'

    
        for num_epochs in epochs:
            for batch_size in batch_sizes:
                for num_layer in nl:
                    # create the model
                    model = Sequential()
                    model.add(LSTM(num_layer, input_shape=(X_train.shape[1], X_train.shape[2])))  ##input_shape=(X_train.shape[1], X_train.shape[2])
                    # model.add(Dropout(0.2))
                    #model.add(Dense(2))
                    model.add(Dense(nc, activation='softmax'))

                    model.compile(loss=loss_type, optimizer='adam', metrics=['AUC','Accuracy',
                                                                             'Recall', 
                                                                             'Precision'])
                    model.fit(X_train, y_train, epochs=num_epochs, batch_size=batch_size)
#                    print(model.summary())

                    # Final evaluation of the model
                    scores = model.evaluate(X_test, y_test, verbose=0)
                    #print(scores)
                    auc = scores[1]
                    acc = scores[2]
                    recall = scores[3]
                    precision = scores[4]
                    #print("AUC: %.2f%%" % (auc))
                    
                    model_name='clf_lstm_{}_{}_b{}_ep{}_h{}'.format(y_type, time_step, batch_size, num_epochs, num_layer)
                    model.save(path+'/{}.h5'.format(model_name))
                    current_result = {'model':model_name,
                                      'precision': precision,  #"%.2f%%" % (precision)
                                      'recall': recall,
                                      'accuracy': acc,
                                      'auc': auc
                                     }
                    results.append(current_result)

                    if auc > best_auc:
                        best_auc = auc
                        best_params = current_result

#    print("Best AUC: ", best_params)
    return results


In [5]:
y_types = ['y_agg','y_oecd']
thresholds=[0.2,0.3,0.4,0.5]
criteria=None
test_year=5

## select imputed & transformed data
X=pd.read_csv('../data/X_data_tr.csv', index_col='date', parse_dates=True)
y=pd.read_csv('../data/y_data_tr.csv', index_col='date', parse_dates=True)
metadata=pd.read_csv('../data/full_info.csv')

final_results=pd.DataFrame()

for i, threshold in enumerate(thresholds):
    df_feature=select_features(metadata, X, threshold, criteria=criteria)
    selected_features=list(df_feature[df_feature.select==1]['variable'])
    print(threshold, selected_features, len(selected_features))
    
    path='../result/ft_{}_{}_ls'.format(str(criteria), str(threshold))

    if not os.path.exists(path):
        os.mkdir(path)
        
    for y_type in y_types:
        X_train, y_train, X_test, y_test = get_data(X, y, y_type, test_year, selected_features)
        
        results=grid_search(path, X_train, y_train, X_test, y_test, y_type, nl=[50,100],  epochs=[300,500], batch_sizes=[5], time_steps=[18,24])
#        results=grid_search(path, X_train, y_train, X_test, y_test, y_type, nl=[5],  epochs=[10], batch_sizes=[5], time_steps=[1,2])

        df_result=pd.DataFrame(results)
        df_result['ft_criteria']=criteria
        df_result['ft_threshold']=threshold
        
        final_results=pd.concat([final_results, df_result])

with open('../result/df_lstm_creport.pkl', 'wb') as f:
    pickle.dump(final_results, f)

    # print(grid_search(X_train, y_train, X_test, y_test, y_type, nl=[50,100],  epochs=[300,500], batch_sizes=[5], time_steps=[18,24]))
    ## ,  epochs=[100,300], batch_sizes=[5,10], time_steps=[18,24]



0.2 ['IPMANSICS', 'PAYEMS', 'HOUST', 'ISRATIOx', 'AMDMUOx', 'T10YFFM', 'GS1', 'CPIAUCNS', 'WILL5000INDFC', 'S&P PE ratio', 'BSI', 'H8B1151NCBCMG'] 12
Epoch 1/300
102/102 [==============================] - 2s 4ms/step - loss: 0.6799 - auc: 0.8730 - Accuracy: 0.6961 - recall: 0.6176 - precision: 0.7241
Epoch 2/300
102/102 [==============================] - 0s 3ms/step - loss: 0.5575 - auc: 0.9128 - Accuracy: 0.7667 - recall: 0.7235 - precision: 0.7987
Epoch 3/300
102/102 [==============================] - 0s 3ms/step - loss: 0.4673 - auc: 0.9409 - Accuracy: 0.7941 - recall: 0.7627 - precision: 0.8121
Epoch 4/300
102/102 [==============================] - 0s 3ms/step - loss: 0.3972 - auc: 0.9559 - Accuracy: 0.8510 - recall: 0.8333 - precision: 0.8586
Epoch 5/300
102/102 [==============================] - 0s 3ms/step - loss: 0.3336 - auc: 0.9712 - Accuracy: 0.8725 - recall: 0.8608 - precision: 0.8780
Epoch 6/300
102/102 [==============================] - 0s 3ms/step - loss: 0.3082 - auc: 0

102/102 [==============================] - 0s 3ms/step - loss: 0.0429 - auc: 0.9995 - Accuracy: 0.9843 - recall: 0.9824 - precision: 0.9843
Epoch 54/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0171 - auc: 1.0000 - Accuracy: 0.9980 - recall: 0.9980 - precision: 0.9980
Epoch 55/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0360 - auc: 0.9996 - Accuracy: 0.9882 - recall: 0.9882 - precision: 0.9882
Epoch 56/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0491 - auc: 0.9985 - Accuracy: 0.9824 - recall: 0.9824 - precision: 0.9824
Epoch 57/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0237 - auc: 0.9999 - Accuracy: 0.9941 - recall: 0.9941 - precision: 0.9941
Epoch 58/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0134 - auc: 1.0000 - Accuracy: 0.9961 - recall: 0.9961 - precision: 0.9961
Epoch 59/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0221 - auc: 0.999

102/102 [==============================] - 0s 3ms/step - loss: 0.0117 - auc: 1.0000 - Accuracy: 0.9961 - recall: 0.9961 - precision: 0.9961
Epoch 107/300
102/102 [==============================] - 0s 4ms/step - loss: 0.0140 - auc: 0.9999 - Accuracy: 0.9961 - recall: 0.9961 - precision: 0.9961
Epoch 108/300
102/102 [==============================] - 0s 4ms/step - loss: 0.0039 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 109/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0034 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 110/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0107 - auc: 1.0000 - Accuracy: 0.9941 - recall: 0.9941 - precision: 0.9941
Epoch 111/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0217 - auc: 0.9998 - Accuracy: 0.9941 - recall: 0.9941 - precision: 0.9941
Epoch 112/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0121 - auc:

102/102 [==============================] - 0s 3ms/step - loss: 0.0160 - auc: 1.0000 - Accuracy: 0.9980 - recall: 0.9980 - precision: 0.9980
Epoch 159/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0241 - auc: 0.9997 - Accuracy: 0.9941 - recall: 0.9941 - precision: 0.9941
Epoch 160/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0110 - auc: 1.0000 - Accuracy: 0.9980 - recall: 0.9980 - precision: 0.9980
Epoch 161/300
102/102 [==============================] - 0s 4ms/step - loss: 0.0066 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 162/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0089 - auc: 1.0000 - Accuracy: 0.9961 - recall: 0.9961 - precision: 0.9961
Epoch 163/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0084 - auc: 1.0000 - Accuracy: 0.9961 - recall: 0.9961 - precision: 0.9961
Epoch 164/300
102/102 [==============================] - 0s 3ms/step - loss: 0.0029 - auc:

102/102 [==============================] - 0s 3ms/step - loss: 9.3944e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 211/300
102/102 [==============================] - 0s 3ms/step - loss: 8.8642e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 212/300
102/102 [==============================] - 0s 3ms/step - loss: 8.4098e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 213/300
102/102 [==============================] - 0s 3ms/step - loss: 7.9673e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 214/300
102/102 [==============================] - 0s 3ms/step - loss: 7.6976e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 215/300
102/102 [==============================] - 0s 3ms/step - loss: 7.2474e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 216/300
102/102 [==============================] - 0s 3ms/st

...

101/101 [==============================] - 2s 18ms/step - loss: 0.0017 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 251/500
101/101 [==============================] - 2s 17ms/step - loss: 0.0014 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 252/500
101/101 [==============================] - 2s 17ms/step - loss: 0.0013 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 253/500
101/101 [==============================] - 2s 19ms/step - loss: 0.0011 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 254/500
101/101 [==============================] - 2s 16ms/step - loss: 0.0010 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 255/500
101/101 [==============================] - 2s 16ms/step - loss: 9.2300e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 256/500
101/101 [==============================] - 2s 17ms/step - loss: 8.

101/101 [==============================] - 2s 21ms/step - loss: 8.4685e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 303/500
101/101 [==============================] - 2s 17ms/step - loss: 7.9217e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 304/500
101/101 [==============================] - 2s 17ms/step - loss: 7.4192e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 305/500
101/101 [==============================] - 2s 18ms/step - loss: 6.9840e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 306/500
101/101 [==============================] - 2s 16ms/step - loss: 6.5114e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 307/500
101/101 [==============================] - 2s 16ms/step - loss: 6.2841e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 308/500
101/101 [==============================] - 2s 

101/101 [==============================] - 2s 16ms/step - loss: 4.4018e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 354/500
101/101 [==============================] - 2s 16ms/step - loss: 4.2369e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 355/500
101/101 [==============================] - 2s 17ms/step - loss: 3.9039e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 356/500
101/101 [==============================] - 2s 17ms/step - loss: 3.8063e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 357/500
101/101 [==============================] - 2s 17ms/step - loss: 3.5558e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 358/500
101/101 [==============================] - 2s 17ms/step - loss: 3.4061e-06 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 359/500
101/101 [==============================] - 2s 

101/101 [==============================] - 2s 17ms/step - loss: 2.3800e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 405/500
101/101 [==============================] - 3s 32ms/step - loss: 2.2092e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 406/500
101/101 [==============================] - 2s 23ms/step - loss: 2.0952e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 407/500
101/101 [==============================] - 2s 18ms/step - loss: 1.9922e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 408/500
101/101 [==============================] - 2s 16ms/step - loss: 1.8476e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 409/500
101/101 [==============================] - 2s 16ms/step - loss: 1.7722e-04 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 410/500
101/101 [==============================] - 2s 

101/101 [==============================] - 2s 16ms/step - loss: 1.4560e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 456/500
101/101 [==============================] - 2s 16ms/step - loss: 1.3874e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 457/500
101/101 [==============================] - 2s 17ms/step - loss: 1.3166e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 458/500
101/101 [==============================] - 2s 17ms/step - loss: 1.2439e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 459/500
101/101 [==============================] - 2s 17ms/step - loss: 1.1761e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 460/500
101/101 [==============================] - 2s 17ms/step - loss: 1.1171e-05 - auc: 1.0000 - Accuracy: 1.0000 - recall: 1.0000 - precision: 1.0000
Epoch 461/500
101/101 [==============================] - 2s 

In [6]:
with open('../result/df_lstm_creport.pkl', 'rb') as f:
    df_lstm_report=pickle.load(f)

df_lstm_report

model  precision    recall  accuracy       auc  \
0     clf_lstm_y_agg_18_b5_ep300_h50   0.690476  0.690476  0.690476  0.731859   
1    clf_lstm_y_agg_18_b5_ep300_h100   0.642857  0.642857  0.642857  0.778345   
2     clf_lstm_y_agg_18_b5_ep500_h50   0.500000  0.500000  0.500000  0.677438   
3    clf_lstm_y_agg_18_b5_ep500_h100   0.690476  0.690476  0.690476  0.851191   
4     clf_lstm_y_agg_24_b5_ep300_h50   0.722222  0.722222  0.722222  0.786265   
..                               ...        ...       ...       ...       ...   
3   clf_lstm_y_oecd_18_b5_ep500_h100   0.571429  0.571429  0.571429  0.625850   
4    clf_lstm_y_oecd_24_b5_ep300_h50   0.416667  0.416667  0.416667  0.482253   
5   clf_lstm_y_oecd_24_b5_ep300_h100   0.638889  0.638889  0.638889  0.619985   
6    clf_lstm_y_oecd_24_b5_ep500_h50   0.583333  0.583333  0.583333  0.653549   
7   clf_lstm_y_oecd_24_b5_ep500_h100   0.555556  0.555556  0.555556  0.570988   

   ft_criteria  ft_threshold  
0         None           0.2  
1         None           0.2  
2         None           0.2  
3         None           0.2  
4         None           0.2  
..         ...           ...  
3         None           0.5  
4         None           0.5  
5         None           0.5  
6         None           0.5  
7         None           0.5  

[64 rows x 7 columns]

In [8]:
# with open('../result/df_lstm_creport.pkl', 'rb') as f:
#     final_results=pickle.load(f)

# clf_lstm_y_oecd_3_b5_ep2_h4

In [ ]:
# y_type = 'y_oecd'
# X_train, y_train, X_test, y_test = get_data(y_type, 5, selected_features)

# # print(grid_search(X_train, y_train, X_test, y_test, y_type, nl=[10,20],  epochs=[5,10], batch_sizes=[5], time_steps=[18]))
# ## ,  epochs=[100,300], batch_sizes=[5,10], time_steps=[18,24]

# result_dict_oecd=grid_search(X_train, y_train, X_test, y_test, y_type, nl=[10],  epochs=[10], batch_sizes=[5], time_steps=[18])

In [ ]:
# pd.DataFrame(result_dict_agg)

In [ ]:
# pd.DataFrame(result_dict_oecd)

In [ ]:

# model2=result_dict[1]['model']

# print(model, model2)

# dir(model)
# model.summary()

In [ ]:
# !pip uninstall shap
# !pip install shap

In [ ]:
# import pickle
# with open('../result/result_dict_agg.pkl','wb') as f:
#     pickle.dump(result_dict_agg, f)

# with open('../result/result_dict_oecd.pkl','wb') as f:
#     pickle.dump(result_dict_oecd, f)


In [ ]:
# !pip uninstall numba
# #!pip install --upgrade numba

In [ ]:
#import shap
# import model_team14 
# from model_team14 import *  ##select_features, plot_pca, DTW

# import os
# import pandas as pd
# import numpy as np
# import pickle
# import matplotlib as mpl
# import matplotlib.pyplot as plt
# from sklearn.preprocessing import label_binarize
# from sklearn.metrics import confusion_matrix,accuracy_score, recall_score, precision_score, f1_score,classification_report 
# from sklearn.metrics import roc_curve, auc

# import seaborn as sns


In [ ]:
# model.predict(np.array(X_test_shap))
# model.fit(np.array(X_test_shap), np.array(y_train_shap))
# model.summary()
# X_train_shap.shape, X_train.shape

In [ ]:
# ##https://stackoverflow.com/questions/66814523/shap-deepexplainer-with-tensorflow-2-4-error?noredirect=1
# ## this might be helpful your debugging!!!

# import shap
# import pickle
# tf.compat.v1.disable_v2_behavior()  ## input type err solved

# # import tensorflow.compat.v1.keras.backend as K
# # import tensorflow as tf
# # tf.compat.v1.disable_eager_execution()
# # tf version is 2.3.1
# # kerase version is 2.4.0
# # Shap version is 0.36

# # with open ('../result/result_dict_oecd.pkl','rb') as f:
# #     result_dict_oecd=pickle.load(f)

# model=result_dict_oecd[0]['model']

# y_type = 'y_oecd'
# X_train, y_train, X_test, y_test = get_data(y_type, 5, selected_features)


# X_train_shap, y_train_shap = create_dataset(X_train, y_train, 18)
# X_test_shap, y_test_shap = create_dataset(X_test, y_test, 18)

# y_train_shap = to_categorical(y_train_shap, num_classes=2)
# y_test_shap = to_categorical(y_test_shap, num_classes=2)

# # X_train_shap=tf.convert_to_tensor(X_train_shap)
# # X_test_shap=tf.convert_to_tensor(X_test_shap)

# X_train_shap=np.array(X_train_shap)
# y_train_shap=np.array(y_train_shap)
# X_test_shap=np.array(X_test_shap)
# y_test_shap=np.array(y_test_shap)

# #type(X_train_shap)
# #X_train

# model.fit(X_train_shap, y_train_shap, batch_size=5, epochs=5)


# X_train_shap2=tf.convert_to_tensor(X_train_shap)
# X_test_shap2=tf.convert_to_tensor(X_test_shap)

# #explainer=shap.DeepExplainer(model, X_train_shap)   #works!

# explainer=shap.DeepExplainer(model, X_train_shap)   #works!

# values=explainer.shap_values(np.array(X_test_shap))



In [ ]:
# shap.initjs()
# shap.force_plot(explainer.expected_value[0], values[0][35], selected_features)

In [ ]:
# shap.initjs()
# shap.force_plot(explainer.expected_value[1], values[0][35], selected_features)

In [ ]:
# dir(explainer)
# explainer.expected_value

In [ ]:
# ##https://stackoverflow.com/questions/66814523/shap-deepexplainer-with-tensorflow-2-4-error?noredirect=1
# ## this might be helpful your debugging!!!

# import shap
# import pickle
# tf.compat.v1.disable_v2_behavior()  ## input type err solved

# # import tensorflow.compat.v1.keras.backend as K
# # import tensorflow as tf
# # tf.compat.v1.disable_eager_execution()
# # tf version is 2.3.1
# # kerase version is 2.4.0
# # Shap version is 0.36

# # with open ('../result/result_dict_oecd.pkl','rb') as f:
# #     result_dict_oecd=pickle.load(f)


# y_type = 'y_oecd'
# X_train, y_train, X_test, y_test = get_data(y_type, 5, selected_features)


# X_train_shap, y_train_shap = create_dataset(X_train, y_train, 18)
# X_test_shap, y_test_shap = create_dataset(X_test, y_test, 18)

# y_train_shap = to_categorical(y_train_shap, num_classes=2)
# y_test_shap = to_categorical(y_test_shap, num_classes=2)

# # X_train_shap=tf.convert_to_tensor(X_train_shap)
# # X_test_shap=tf.convert_to_tensor(X_test_shap)

# X_train_shap=np.array(X_train_shap)
# y_train_shap=np.array(y_train_shap)
# X_test_shap=np.array(X_test_shap)
# y_test_shap=np.array(y_test_shap)

# #type(X_train_shap)
# #X_train

# new_model.fit(X_train_shap, y_train_shap, batch_size=5, epochs=5)


# X_train_shap2=tf.convert_to_tensor(X_train_shap)
# X_test_shap2=tf.convert_to_tensor(X_test_shap)

# #explainer=shap.DeepExplainer(model, X_train_shap)   #works!

# explainer=shap.DeepExplainer(new_model, X_train_shap)   #works!

# values=explainer.shap_values(np.array(X_test_shap))



In [ ]:
# explainer.expected_value

In [ ]:
# # values[0].shape
# # shap.summary_plot(values[0], X_test_shap)
# # values[0]
# shap.initjs()
# shap.force_plot(explainer.expected_value[0], values[0][35], selected_features)